In [1]:
!pip install mlflow  optuna  lightgbm dagshub

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.7/24.7 MB 75.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.9/1.9 MB 73.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 395.9/395.9 kB 13.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 261.0/261.0 kB 17.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 247.0/247.0 kB 20.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 147.8/147.8 kB 11.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 114.9/114.9 kB 9.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 85.0/85.0 kB 7.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 139.9/139.9 kB 11.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 96.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 741.4/741.4 kB 42.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 203.4/203.4 kB 17.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

In [2]:
import dagshub
import mlflow
dagshub.init(repo_owner='AMR-ITH', repo_name='yt-comment-analyzer', mlflow=True)

❗❗❗ AUTHORIZATION REQUIRED ❗❗❗



Open the following link in your browser to authorize the client:
https://dagshub.com/login/oauth/authorize?state=bc825615-c0a7-4767-a462-2cdf24122573&client_id=32b60ba385aa7cecf24046d8195a71c07dd345d9657977863b52e7748e0f0f28&middleman_request_id=1fcf287cacf647c379d4ecf6cc80a036c62ae3df3b3e77ebce166df7d9bff71b




Output()

Accessing as AMR-ITH

Initialized MLflow to track repo "AMR-ITH/yt-comment-analyzer"

Repository AMR-ITH/yt-comment-analyzer initialized!

In [3]:
# Set or create an experiment
mlflow.set_experiment("exp6 Top model HP Tuning")

<Experiment: artifact_location='mlflow-artifacts:/bf3d95fd04174c5fb2927f776d1cad69', creation_time=1752407354692, experiment_id='11', last_update_time=1752407354692, lifecycle_stage='active', name='exp6 Top model HP Tuning', tags={}>

In [15]:
import pandas as pd
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, classification_report
import mlflow
import mlflow.sklearn
import optuna
from lightgbm import LGBMClassifier
import matplotlib.pyplot as plt

In [5]:
df = pd.read_csv("/content/reddit_preprocessing.csv").dropna()
df.head()

clean_comment  category
0  family mormon never tried explain still stare ...         1
1  buddhism much lot compatible christianity espe...         1
2  seriously say thing first get complex explain ...        -1
3  learned want teach different focus goal not wr...         0
4  benefit may want read living buddha living chr...         1

In [10]:
df.shape

(36662, 2)

In [11]:
# Step 1: Clean data
df = df.dropna(subset=['category'])
y = df['category'].map({-1: 2, 0: 0, 1: 1})
X_raw = df['clean_comment']

# Step 2: Train-test split BEFORE vectorization or resampling
X_train_raw, X_test_raw, y_train, y_test = train_test_split(
    X_raw, y, test_size=0.2, random_state=42, stratify=y
)

# Function to log results in MLflow
def log_mlflow(model_name, model, X_train, X_test, y_train, y_test, params, trial_number, max_features):
    with mlflow.start_run():
        # Log model type and trial number with max_features
        mlflow.set_tag("mlflow.runName", f"Trial_{trial_number}_{model_name}_TFIDF_Trigrams_MaxFeatures_{max_features}")
        mlflow.set_tag("experiment_type", "algorithm_comparison")

        # Log algorithm name as a parameter
        mlflow.log_param("algo_name", model_name)
        mlflow.log_param("max_features", max_features)

        # Log hyperparameters
        for key, value in params.items():
            mlflow.log_param(key, value)

        # Train model
        model.fit(X_train, y_train)
        y_pred = model.predict(X_test)

        # Log accuracy
        accuracy = accuracy_score(y_test, y_pred)
        mlflow.log_metric("accuracy", accuracy)

        # Log classification report
        classification_rep = classification_report(y_test, y_pred, output_dict=True)
        for label, metrics in classification_rep.items():
            if isinstance(metrics, dict):
                for metric, value in metrics.items():
                    mlflow.log_metric(f"{label}_{metric}", value)

        # Save and log the model manually using joblib
        import joblib
        model_filename = "LightGBM_trial_Best.pkl"
        joblib.dump(model, model_filename)
        mlflow.log_artifact(model_filename)

        return accuracy



In [12]:
# Step 6: Optuna objective function for LightGBM
def objective_lightgbm(trial, X_train, X_test, max_features):
    # Hyperparameter space to explore
    n_estimators = trial.suggest_int('n_estimators', 100, 1000)
    learning_rate = trial.suggest_float('learning_rate', 1e-4, 1e-1, log=True)
    max_depth = trial.suggest_int('max_depth', 3, 15)
    num_leaves = trial.suggest_int('num_leaves', 20, 150)
    min_child_samples = trial.suggest_int('min_child_samples', 10, 100)
    colsample_bytree = trial.suggest_float('colsample_bytree', 0.5, 1.0)
    subsample = trial.suggest_float('subsample', 0.5, 1.0)
    reg_alpha = trial.suggest_float('reg_alpha', 1e-4, 10.0, log=True)  # L1 regularization
    reg_lambda = trial.suggest_float('reg_lambda', 1e-4, 10.0, log=True)  # L2 regularization

    # Log trial parameters
    params = {
        'n_estimators': n_estimators,
        'learning_rate': learning_rate,
        'max_depth': max_depth,
        'num_leaves': num_leaves,
        'min_child_samples': min_child_samples,
        'colsample_bytree': colsample_bytree,
        'subsample': subsample,
        'reg_alpha': reg_alpha,
        'reg_lambda': reg_lambda
    }

    # Create LightGBM model
    model = LGBMClassifier(n_estimators=n_estimators,
                           learning_rate=learning_rate,
                           max_depth=max_depth,
                           num_leaves=num_leaves,
                           min_child_samples=min_child_samples,
                           colsample_bytree=colsample_bytree,
                           subsample=subsample,
                           reg_alpha=reg_alpha,
                           reg_lambda=reg_lambda,
                           is_unbalance=True,
                           random_state=42)

    # Log each trial as a separate run in MLflow
    # accuracy = log_mlflow("LightGBM", model, X_train, X_test, y_train, y_test, params, trial.number, max_features)

    # return accuracy
    model.fit(X_train, y_train)
    preds = model.predict(X_test)
    return accuracy_score(y_test, preds)


In [13]:
# Step 7: Run Optuna for LightGBM with different max_features values
def run_optuna_experiment():
    max_features_list = [ 10000]

    for max_features in max_features_list:
        print(f"\n=== Running experiment with max_features={max_features} ===")

        # Step 3: Vectorization only on training data with current max_features
        vectorizer = TfidfVectorizer(ngram_range=(1, 3), max_features=max_features)
        X_train = vectorizer.fit_transform(X_train_raw)
        X_test = vectorizer.transform(X_test_raw) # only transform

        # Create study for current max_features
        study = optuna.create_study(direction="maximize")
        study.optimize(lambda trial: objective_lightgbm(trial, X_train, X_test, max_features),
                      n_trials=100)

        # Get the best parameters
        best_params = study.best_params
        best_model = LGBMClassifier(n_estimators=best_params['n_estimators'],
                                    learning_rate=best_params['learning_rate'],
                                    max_depth=best_params['max_depth'],
                                    num_leaves=best_params['num_leaves'],
                                    min_child_samples=best_params['min_child_samples'],
                                    colsample_bytree=best_params['colsample_bytree'],
                                    subsample=best_params['subsample'],
                                    reg_alpha=best_params['reg_alpha'],
                                    reg_lambda=best_params['reg_lambda'],
                                    is_unbalance=True,
                                    random_state=42)

        # Log the best model with MLflow and print the classification report
        best_accuracy = log_mlflow("LightGBM", best_model, X_train, X_test, y_train, y_test,
                                  best_params, f"Best-hp-MaxFeatures-{max_features}", max_features)

        print(f"Best accuracy for max_features={max_features}: {best_accuracy:.4f}")
        print(f"Best parameters: {best_params}")

        # Plot parameter importance
        optuna.visualization.plot_param_importances(study).show()

        # Plot optimization history
        optuna.visualization.plot_optimization_history(study).show()



In [ ]:
run_optuna_experiment()


=== Running experiment with max_features=10000 ===


[I 2025-07-13 15:17:40,153] A new study created in memory with name: no-name-2b87fd88-f6d4-48e5-be18-19cb54805a80
/usr/local/lib/python3.11/dist-packages/sklearn/utils/deprecation.py:151: FutureWarning:

'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.



[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.251508 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 92127
[LightGBM] [Info] Number of data points in the train set: 29329, number of used features: 1342
[LightGBM] [Info] Start training from score -1.064557
[LightGBM] [Info] Start training from score -0.843611
[LightGBM] [Info] Start training from score -1.491810
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further 

/usr/local/lib/python3.11/dist-packages/sklearn/utils/deprecation.py:151: FutureWarning:

'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.

[I 2025-07-13 15:18:07,882] Trial 0 finished with value: 0.6529387699440884 and parameters: {'n_estimators': 324, 'learning_rate': 0.0026178969447509482, 'max_depth': 9, 'num_leaves': 20, 'min_child_samples': 67, 'colsample_bytree': 0.5979515772840662, 'subsample': 0.7549208173100588, 'reg_alpha': 0.0017284309293486035, 'reg_lambda': 6.7470501902427396}. Best is trial 0 with value: 0.6529387699440884.
/usr/local/lib/python3.11/dist-packages/sklearn/utils/deprecation.py:151: FutureWarning:

'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.



[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.370905 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 90210
[LightGBM] [Info] Number of data points in the train set: 29329, number of used features: 1263
[LightGBM] [Info] Start training from score -1.064557
[LightGBM] [Info] Start training from score -0.843611
[LightGBM] [Info] Start training from score -1.491810
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further 

...

[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.912533 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 130941
[LightGBM] [Info] Number of data points in the train set: 29329, number of used features: 4402
[LightGBM] [Info] Start training from score -1.064557
[LightGBM] [Info] Start training from score -0.843611
[LightGBM] [Info] Start training from score -1.491810
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further

/usr/local/lib/python3.11/dist-packages/sklearn/utils/deprecation.py:151: FutureWarning:

'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.

[I 2025-07-13 17:30:35,915] Trial 77 finished with value: 0.8633574253375154 and parameters: {'n_estimators': 778, 'learning_rate': 0.0812293654597214, 'max_depth': 15, 'num_leaves': 106, 'min_child_samples': 20, 'colsample_bytree': 0.6327299001447477, 'subsample': 0.8796450206011206, 'reg_alpha': 0.021320141956530383, 'reg_lambda': 0.0074237111300469475}. Best is trial 68 with value: 0.8769944088367653.
/usr/local/lib/python3.11/dist-packages/sklearn/utils/deprecation.py:151: FutureWarning:

'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.



[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 1.441844 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 140165
[LightGBM] [Info] Number of data points in the train set: 29329, number of used features: 5737
[LightGBM] [Info] Start training from score -1.064557
[LightGBM] [Info] Start training from score -0.843611
[LightGBM] [Info] Start training from score -1.491810
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further

/usr/local/lib/python3.11/dist-packages/sklearn/utils/deprecation.py:151: FutureWarning:

'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.

[I 2025-07-13 17:34:27,469] Trial 78 finished with value: 0.8678576298922678 and parameters: {'n_estimators': 658, 'learning_rate': 0.08691010726991522, 'max_depth': 13, 'num_leaves': 122, 'min_child_samples': 15, 'colsample_bytree': 0.5929848715352787, 'subsample': 0.8986972215836915, 'reg_alpha': 0.00847546274711668, 'reg_lambda': 0.1493304872940898}. Best is trial 68 with value: 0.8769944088367653.
/usr/local/lib/python3.11/dist-packages/sklearn/utils/deprecation.py:151: FutureWarning:

'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.



[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 1.931074 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 147962
[LightGBM] [Info] Number of data points in the train set: 29329, number of used features: 7126
[LightGBM] [Info] Start training from score -1.064557
[LightGBM] [Info] Start training from score -0.843611
[LightGBM] [Info] Start training from score -1.491810
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning]